In [24]:
import json
import pandas as pd
import plotly.express as px

import numpy as np

import pandas as pd
import plotly.graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots
from scipy import stats
import numpy as np
import math
df_ag_cases = pd.read_csv('static/csv/be-covid-case-age-sex.csv')
df_ag_cases.dropna(inplace=True)
from datetime import datetime, date, timedelta


# Cases per age group (centered rolling average)

In [28]:
def age_group_cases(prov = 'All'):
    
    df_ag_all = df_ag_cases

    if prov != 'All':
        df_ag_all = df_ag_cases[df_ag_cases['PROVINCE'] == prov]

    idx = pd.date_range(df_ag_all.DATE.min(), df_ag_all.DATE.max())
    bars_age_groups = []
    traces = []
    age_groups = sorted(df_ag_all.AGEGROUP.unique())
    for idx2, ag in enumerate(age_groups):
        df_ag = df_ag_all.loc[df_ag_all['AGEGROUP'] == ag]
        df_ag = df_ag.groupby(['DATE']).agg({'CASES': 'sum'})
        df_ag.index = pd.DatetimeIndex(df_ag.index)
        df_ag = df_ag.reindex(idx, fill_value=0)
        traces.append(go.Scatter(
            x=df_ag.index[:-4],
            y=df_ag['CASES'][:-4].rolling(7,center=True).mean(),
            name=ag,
            showlegend=True,
            legendgroup=ag, stackgroup='one',
            line=dict(width=0.5),
            mode='lines', groupnorm=""))

    fig = go.Figure(data=traces)

    # Edit the layout
    fig.update_layout(title='Age group cases '+prov,
                      xaxis_title='Date',
                      yaxis_title='')
    fig.update_layout(template="plotly_white")

    fig.update_layout(
        updatemenus=[
            dict(
                type="buttons",
                direction="up",
                buttons=list([
                    dict(
                        args=[{"groupnorm": ""}],
                        label="absolute",
                        method="restyle"
                    ),
                    dict(
                        args=[{"groupnorm": "percent"}],
                        label="percent",
                        method="restyle"
                    )
                ]),
            ),
        ])

    return fig



def cases_per_provinces_ag():
    prov = ['All','Liège', 'Brussels','Antwerpen','Namur', 'Luxembourg', 'Hainaut' , 'BrabantWallon', 'VlaamsBrabant', 'OostVlaanderen',
        'WestVlaanderen', 'Limburg',]

    for prov_name in prov:
            fig = age_group_cases(prov=prov_name)
            
            fig.show()



cases_per_provinces_ag()

# Age group case % increase over previous week

In [54]:
#print(df_ag_cases)
def age_group_cases_increase():
    
    df_ag_all = df_ag_cases

    idx = pd.date_range(df_ag_all.DATE.min(), df_ag_all.DATE.max())
    bars_age_groups = []
    traces = []
    data = []
    dates = []
    age_groups = sorted(df_ag_all.AGEGROUP.unique())
    for idx2, ag in enumerate(age_groups):
        df_ag = df_ag_all.loc[df_ag_all['AGEGROUP'] == ag]
        df_ag = df_ag.groupby(['DATE']).agg({'CASES': 'sum'})
        df_ag.index = pd.DatetimeIndex(df_ag.index)
        df_ag = df_ag.reindex(idx, fill_value=0)
        

        today = (df_ag['CASES']).rolling(7).mean().values
        oneweekago = today[:-7]
        ratio = (today[7:] / oneweekago * 100) - 100

        dates = idx[500+7:]

        data.append(ratio[500:])
        ag
        
    import plotly.express as px

    fig = px.imshow(data,y=age_groups,x=dates)

    fig.update_layout(title='Age group cases % increase over one week ',
                      xaxis_title='Date',
                      yaxis_title='Age group')
    fig.update_layout(template="plotly_white")

   

    return fig


age_group_cases_increase()
